<a href="https://colab.research.google.com/github/MylavarapuSaketh/Saketh_INFO5731_Fall2023/blob/main/Mylavarapu_Saketh_Assignment_02.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **INFO5731 Assignment Two**

In this assignment, you will try to gather text data from open data source via web scraping or API. After that you need to clean the text data and syntactic analysis of the data.

# **Question 1**

(40 points). Write a python program to collect text data from **either of the following sources** and save the data into a **csv file**:

(1) Collect all the customer reviews of a product (you can choose any porduct) on amazon.

(2) Collect the top 10000 User Reviews of a film recently in 2023 or 2022 (you can choose any film) from IMDB.

(3) Collect all the reviews of the top 1000 most popular software from [G2](https://www.g2.com/) or [Capterra](https://www.capterra.com/)

(4) Collect the abstracts of the top 10000 research papers by using the query "machine learning", "data science", "artifical intelligence", or "information extraction" from [Semantic Scholar](https://www.semanticscholar.org).

(5) Collect all the information of the 904 narrators in the [Densho Digital Repository](https://ddr.densho.org/narrators/).

(6) Collect the top 10000 reddits by using a hashtag (you can use any hashtag) from Reddits.


In [12]:
# Write your code here
import requests
import csv
from bs4 import BeautifulSoup

# specify the URL of the IMDB page for the RRR movie reviews
url = 'https://www.imdb.com/title/tt8178634/reviews/?ref_=tt_ql_2'

# send a GET request to the URL
response = requests.get(url) # parse the HTML content using Beautiful Soup


soup = BeautifulSoup(response.content, 'html.parser') # find the total number of user reviews


total_reviews_str = soup.find('div', {'class': 'header'}).get_text()
total_reviews_str = total_reviews_str.split()[0] # extract the first word of the string

total_reviews = int(total_reviews_str.replace(',', ''))


csv_file = open('RRR_reviews.csv', 'w', newline='', encoding='utf-8') # create a CSV file to save the data
csv_writer = csv.writer(csv_file)
csv_writer.writerow(['Review'])

# loop through all the pages of reviews and save them in the CSV file
for page in range(1, min(1001, total_reviews // 10 + 2)):# generate the URL for the current page of reviews

    page_url = f'{url}&start={10*(page-1)}'

    page_response = requests.get(page_url)# send a GET request to the page URL

    page_soup = BeautifulSoup(page_response.content, 'html.parser') # parse the HTML content using Beautiful Soup

    reviews = page_soup.find_all('div', {'class': 'text show-more__control'}) # find all the user reviews on the page

    for review in reviews: # loop through all the reviews and save them in the CSV file
        review_text = review.get_text().strip()
        csv_writer.writerow([review_text])

# close the CSV file
csv_file.close()



In [13]:
import pandas as pd

                   # read the CSV file into a DataFrame
df = pd.read_csv('RRR_reviews.csv')

                   # print the first 100 rows of the DataFrame
print(df.head(3000))

                                                 Review
0     I have seen a lot of movies in my time, made i...
1     I bet you'd never think the mash-up the heavy-...
2     I have to try and review this without comparin...
3     There is officially ZERO reason to watch Gray ...
4     When I pushed play, I did not really believe t...
...                                                 ...
2995  RRR is an entertaining movie and is not a bori...
2996  RRR (2022) :\nMovie Review -High and Low. No, ...
2997  Watched it in 3d. Some scenes are like over th...
2998  It's brutal, ridiculous, action-packed, fun, e...
2999  Just watched #RRR. Are u going to read this re...

[3000 rows x 1 columns]


# **Question 2**

(30 points). Write a python program to **clean the text data** you collected above and save the data in a new column in the csv file. The data cleaning steps include:

(1) Remove noise, such as special characters and punctuations.

(2) Remove numbers.

(3) Remove stopwords by using the [stopwords list](https://gist.github.com/sebleier/554280).

(4) Lowercase all texts

(5) Stemming.

(6) Lemmatization.

In [ ]:
# Write your code here
import nltk
nltk.download()

In [23]:
pip install textblob


In [14]:
import re # importing
#PUNCTUATIONS
#1 Noise Remove
df['Reviews after Noise Removal'] = df['Review'].str.replace('[^\w\s]','')
df['Reviews after Noise Removal'] = df['Reviews after Noise Removal'].apply(lambda x: ''.join(re.sub(r"[^a-zA-Z0-9]+", ' ', charctr) for charctr in x ))

<ipython-input-14-5bda00bb5a04>:3: FutureWarning: The default value of regex will change from True to False in a future version.
  df['Reviews after Noise Removal'] = df['Review'].str.replace('[^\w\s]','')


In [15]:
#2 Removing -digits
#DIGITS
df['After digits removal'] = df['Reviews after Noise Removal'].apply(lambda y: ''.join([i for i in y if not i.isdigit()]))

In [16]:
#3 Removing -stop words

from nltk.corpus import stopwords
#STOP WORDS
s = stopwords.words('english')
df['Stopwords Removal'] = df['After digits removal'].apply(lambda x: " ".join(x for x in x.split() if x not in s))

In [26]:
#Convert to lower case
#4 LOWER CASE
df['Lower Case'] = df['Stopwords Removal'].apply(lambda x: " ".join(x.lower() for x in x.split()))
#Stemming

from nltk.stem import PorterStemmer
s = PorterStemmer()

#5 STEMMING
df['After Stemming'] = df['Lower Case'].apply(lambda x: " ".join([s.stem(word) for word in x]))

#6Lemmatization

from textblob import Word
import nltk   #importing
nltk.download('wordnet')
#LEMMATIZATION

df['After Lemmatization'] = df['After Stemming'].apply(lambda x: " ".join([Word(word).lemmatize() for word in x.split()]))
df

[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


Review  \
0     I have seen a lot of movies in my time, made i...   
1     I bet you'd never think the mash-up the heavy-...   
2     I have to try and review this without comparin...   
3     There is officially ZERO reason to watch Gray ...   
4     When I pushed play, I did not really believe t...   
...                                                 ...   
4220  RRR is an entertaining movie and is not a bori...   
4221  RRR (2022) :\nMovie Review -High and Low. No, ...   
4222  Watched it in 3d. Some scenes are like over th...   
4223  It's brutal, ridiculous, action-packed, fun, e...   
4224  Just watched #RRR. Are u going to read this re...   

                            Reviews after Noise Removal  \
0     I have seen a lot of movies in my time made in...   
1     I bet youd never think the mashup the heavyhan...   
2     I have to try and review this without comparin...   
3     There is officially ZERO reason to watch Gray ...   
4     When I pushed play I did not really believe th...   
...                                                 ...   
4220  RRR is an entertaining movie and is not a bori...   
4221  RRR 2022  Movie Review High and Low No Im not ...   
4222  Watched it in 3d Some scenes are like over the...   
4223  Its brutal ridiculous actionpacked fun enterta...   
4224  Just watched RRR Are u going to read this revi...   

                                   After digits removal  \
0     I have seen a lot of movies in my time made in...   
1     I bet youd never think the mashup the heavyhan...   
2     I have to try and review this without comparin...   
3     There is officially ZERO reason to watch Gray ...   
4     When I pushed play I did not really believe th...   
...                                                 ...   
4220  RRR is an entertaining movie and is not a bori...   
4221  RRR   Movie Review High and Low No Im not talk...   
4222  Watched it in d Some scenes are like over the ...   
4223  Its brutal ridiculous actionpacked fun enterta...   
4224  Just watched RRR Are u going to read this revi...   

                                      Stopwords Removal  \
0     I seen lot movies time made lot different styl...   
1     I bet youd never think mashup heavyhanded Ramb...   
2     I try review without comparing anything direct...   
3     There officially ZERO reason watch Gray Man TH...   
4     When I pushed play I really believe I would ev...   
...                                                 ...   
4220  RRR entertaining movie boring watch means Raja...   
4221  RRR Movie Review High Low No Im talking Akira ...   
4222  Watched Some scenes like top illogical You don...   
4223  Its brutal ridiculous actionpacked fun enterta...   
4224  Just watched RRR Are u going read review Revie...   

                                             Lower Case  \
0     i seen lot movies time made lot different styl...   
1     i bet youd never think mashup heavyhanded ramb...   
2     i try review without comparing anything direct...   
3     there officially zero reason watch gray man th...   
4     when i pushed play i really believe i would ev...   
...                                                 ...   
4220  rrr entertaining movie boring watch means raja...   
4221  rrr movie review high low no im talking akira ...   
4222  watched some scenes like top illogical you don...   
4223  its brutal ridiculous actionpacked fun enterta...   
4224  just watched rrr are u going read review revie...   

                                         After Stemming  \
0     i   s e e n   l o t   m o v i e s   t i m e   ...   
1     i   b e t   y o u d   n e v e r   t h i n k   ...   
2     i   t r y   r e v i e w   w i t h o u t   c o ...   
3     t h e r e   o f f i c i a l l y   z e r o   r ...   
4     w h e n   i   p u s h e d   p l a y   i   r e ...   
...                                                 ...   
4220  r r r   e n t e r t a i n i n g   m o v i e   ...   
4221  r r r   m o v i e   r e v 

In [20]:
df.to_csv('RRR1_reviews.csv', index=False)


# **Question 3**

(30 points). Write a python program to conduct **syntax and structure analysis** of the clean text you just saved above. The syntax and structure analysis includes:

(1) Parts of Speech (POS) Tagging: Tag Parts of Speech of each word in the text, and calculate the total number of N(oun), V(erb), Adj(ective), Adv(erb), respectively.

(2) Constituency Parsing and Dependency Parsing: print out the constituency parsing trees and dependency parsing trees of all the sentences. Using one sentence as an example to explain your understanding about the constituency parsing tree and dependency parsing tree.

(3) Named Entity Recognition: Extract all the entities such as person names, organizations, locations, product names, and date from the clean texts, calculate the count of each entity.

In [27]:
# Write your code here

from nltk.tokenize import word_tokenize
p = []
#for statement
for sentence in df['Lower Case']:
  text = word_tokenize(sentence)
  p.append(nltk.pos_tag(text)) #appending
p


[[('i', 'NN'),
  ('seen', 'VBN'),
  ('lot', 'NN'),
  ('movies', 'NNS'),
  ('time', 'NN'),
  ('made', 'VBN'),
  ('lot', 'NN'),
  ('different', 'JJ'),
  ('styles', 'NNS'),
  ('different', 'JJ'),
  ('genres', 'NNS'),
  ('around', 'IN'),
  ('world', 'NN'),
  ('ive', 'VBP'),
  ('seen', 'VBN'),
  ('everything', 'NN'),
  ('mainstream', 'JJ'),
  ('movie', 'NN'),
  ('imaginable', 'JJ'),
  ('experimental', 'JJ'),
  ('i', 'NN'),
  ('cant', 'VBP'),
  ('even', 'RB'),
  ('remember', 'VB'),
  ('last', 'JJ'),
  ('time', 'NN'),
  ('i', 'NN'),
  ('came', 'VBD'),
  ('away', 'RB'),
  ('movie', 'NN'),
  ('thinking', 'VBG'),
  ('id', 'NN'),
  ('never', 'RB'),
  ('seen', 'VBN'),
  ('anything', 'NN'),
  ('like', 'IN'),
  ('but', 'CC'),
  ('thats', 'NNS'),
  ('i', 'VBP'),
  ('felt', 'VBD'),
  ('rrrthis', 'JJ'),
  ('movie', 'NN'),
  ('much', 'JJ'),
  ('its', 'PRP$'),
  ('muchness', 'NN'),
  ('may', 'MD'),
  ('turn', 'VB'),
  ('almost', 'RB'),
  ('my', 'PRP$'),
  ('wife', 'NN'),
  ('i', 'VBP'),
  ('nearly', 'RB'

**Write your explanations of the constituency parsing tree and dependency parsing tree here (Question 3-2):**


In [30]:
'''
Constituency Parsing Tree:

A constituency parsing tree, also known as a syntactic or phrase structure tree, represents the hierarchical structure of a sentence or text in terms of its constituents or phrases. Each node in the tree corresponds to a phrase, and the edges between nodes represent the syntactic relationships between these phrases. lets use the sentence "The quick brown fox jumps over the lazy dog" as an example to explain both the constituency parsing tree and the dependency parsing tree. In the constituency parsing tree, we break down the sentence into its constituent phrases, showing the hierarchical structure:

The whole sentence is the root of the tree.
"The quick brown fox" forms a noun phrase (NP), which is a subtree.
"jumps over" is a verb phrase (VP), which is also a subtree.
Within "The quick brown fox," each word is a leaf node.
"over" is a preposition (P) that forms a prepositional phrase (PP) with "the lazy dog."
In the dependency parsing tree, we represent the grammatical relationships between words. The sentence's structure is revealed through dependencies:

"jumps" is the root of the tree, as it's the main verb.
"fox" is the subject (nsubj) of "jumps," indicating that it's the one performing the action.
"quick" and "brown" are adjectives (amod) describing "fox."
"over" is a preposition (prep), and "dog" is its object (pobj). "The" and "lazy" modify "dog."
 '''

' \nConstituency Parsing Tree:\n\nA constituency parsing tree, also known as a syntactic or phrase structure tree, represents the hierarchical structure of a sentence or text in terms of its constituents or phrases. Each node in the tree corresponds to a phrase, and the edges between nodes represent the syntactic relationships between these phrases. lets use the sentence "The quick brown fox jumps over the lazy dog" as an example to explain both the constituency parsing tree and the dependency parsing tree. In the constituency parsing tree, we break down the sentence into its constituent phrases, showing the hierarchical structure:\n\nThe whole sentence is the root of the tree.\n"The quick brown fox" forms a noun phrase (NP), which is a subtree.\n"jumps over" is a verb phrase (VP), which is also a subtree.\nWithin "The quick brown fox," each word is a leaf node.\n"over" is a preposition (P) that forms a prepositional phrase (PP) with "the lazy dog."\nIn the dependency parsing tree, we 